# Tensorflow Extended (TFX) Demo 
---

### Running a Pipeline Manually 

In this notebook we will create a TFX pipeline that can be orchestrated manually. The goal with running the pipeline in an interactive context is to easily visualize some of the features of TFX. We will be able to, for example, inspect the inputs and outputs to each component, investigate how data is being written to the metadata store, and demystify some what is happening under the hood in the TFX components. Furthermore, this type of workflow could also potentially be used for some late stage experimentation with feature engineering and modelling in the same place that we develop pipelines. 

In a production deployment of TFX we would use an orchestrator such as Apache Airflow, Kubeflow Pipelines, or Apache Beam. In an interactive notebook the notebook itself is the orchestrator, running each TFX component as the notebook cells are executed. For development this provides another alternative to running airflow locally. Another difference when using the interactive context is how we access metadata through the ML Metadata (MLMD) api. Typically these metadata properties would be stored in a database such as MySQL (Cloud SQL) and the metadata payloads would be stored in a persistent store on our filesystem (or GCS). In our interactive notebook, we will store everything in an ephemeral SQLite database. 

We will go through most of the TFX components in this notebook. We will not "just" run each one, but rather take some time to explore the inputs and outputs of each component to gain some understanding of what is going on. Without taking the time to explore inputs and outputs, there really is no advantage to using the interactive context and instead we could run Airflow locally for development purposes. 

In [1]:
import os
import pprint
import tempfile
import urllib

import pandas as pd
from sklearn.model_selection import train_test_split

import absl
import tensorflow as tf
import tensorflow_model_analysis as tfma
import tensorflow_data_validation as tfdv
import tensorflow_transform as tft
tf.get_logger().propagate = False
pp = pprint.PrettyPrinter()

import tfx
from tfx.components import CsvExampleGen
from tfx.components import Evaluator
from tfx.components import ExampleValidator
from tfx.components import Pusher
from tfx.components import ResolverNode
from tfx.components import SchemaGen
from tfx.components import StatisticsGen
from tfx.components import Trainer
from tfx.components import Transform
from tfx.components.base import executor_spec
from tfx.components.trainer.executor import GenericExecutor
from tfx.dsl.experimental import latest_blessed_model_resolver
from tfx.orchestration import metadata
from tfx.orchestration import pipeline
from tfx.orchestration.experimental.interactive.interactive_context import InteractiveContext
from tfx.components.example_gen.custom_executors import parquet_executor 
from tfx.components.example_gen.component import FileBasedExampleGen

from tfx.proto import pusher_pb2
from tfx.proto import trainer_pb2
from tfx.proto import example_gen_pb2

from tensorflow_metadata.proto.v0 import schema_pb2 
from tensorflow_metadata.proto.v0 import statistics_pb2
from tensorflow_metadata.proto.v0 import anomalies_pb2

from ml_metadata import metadata_store
from ml_metadata.proto import metadata_store_pb2

import tensorflow_data_validation as tfdv 
import tensorflow_transform as tft
import tensorflow_model_analysis as tfma

from tfx.types import Channel
from tfx.types.standard_artifacts import Model
from tfx.types.standard_artifacts import ModelBlessing
from tfx.utils.dsl_utils import external_input

/home/jupyter/venv/lib/python3.7/site-packages/tfx/orchestration/data_types.py:191: UserWarning: RuntimeParameter is only supported on KubeflowDagRunner currently.
  warnings.warn('RuntimeParameter is only supported on KubeflowDagRunner '


Run with: 
```
TensorFlow version: 2.3.0
TFX version: 0.24.1
TFT version: 0.24.1
TFDV version: 0.24.1
TFMA version: 0.24.3
```

In [2]:
print('TensorFlow version: {}'.format(tf.__version__))
print('TFX version: {}'.format(tfx.__version__))
print('TFT version: {}'.format(tft.__version__))
print('TFDV version: {}'.format(tfdv.__version__))
print('TFMA version: {}'.format(tfma.__version__))

TensorFlow version: 2.3.0
TFX version: 0.24.1
TFT version: 0.24.1
TFDV version: 0.24.1
TFMA version: 0.24.3


Create a new jupyter kernel based on Pipfile

### **Pre-Preprocessing** 

The following cell is lifted from the original research notebooks. As a prerequisite to being able to run our training pipeline, we will assume that we have some files in cloud storage that are ready for the real preprocessing (as found in the `preprocessing_fn` in our `Preprocessing.ipynb` notebook). 

Of course, these steps will eventually need to be incorporated into a data processing pipeline. It is possible that a few of the steps could be incorporated into the preprocessing in case these steps are replicated on the serving side. For now, though, we will assume that we have the data ready to go. 

In [ ]:
translated = pd.read_csv("gs://ml-sandbox-101-tagging/data/processed/translation_data/translated_data_entode.csv", index_col=0)
overlap = pd.read_csv("gs://ml-sandbox-101-tagging/data/processed/de_gb_overlap_data.csv", index_col=0)

overlap.rename(columns={"combi":"full_translated"}, inplace=True)
overlap = pd.merge(translated,overlap,how='left',on='TitleId')

overlap['features'] = overlap[['full_translated_x','full_translated_y','series_ep_subgenre_y']].fillna("").apply(" ".join, axis=1)
train_data_all =  overlap[['TitleId', 'series_ep_uuid_x', 'title_x', 'series_ep_title_x',
       'series_name_x', 'series_ep_synopsis_x', 'genre_x',
       'series_ep_subgenre_x', 'series_ep_tags_x','translated_text',
       'tranlsated_subgenres', 'tranlsated_tags',  'features']]

train_data_all.rename(columns={'series_ep_uuid_x':'series_ep_uuid',
                               'title_x':'title', 
                               'series_ep_title_x':'series_ep_title',
                               'series_name_x':'series_name', 
                               'series_ep_synopsis_x':'series_ep_synopsis', 
                               'genre_x':'genre',
                               'series_ep_subgenre_x':'series_ep_subgenre', 
                               'series_ep_tags_x':'series_ep_tags'},inplace=True)

train_data_all = train_data_all[train_data_all.features.apply(len)>30]

# split train/test uuids
train_uuids,test_uuids = train_test_split(train_data_all.series_ep_uuid.unique(), shuffle=True, test_size=0.1, random_state=42)
# We take a series and we want it all to go in training or all in testing avoid any possible leakage

train_data_all['series_ep_tags'] = train_data_all['series_ep_tags'].apply(lambda x: eval(x))

train_data = train_data_all.loc[train_data_all.series_ep_uuid.isin(train_uuids),:].copy()
test_data = train_data_all.loc[train_data_all.series_ep_uuid.isin(test_uuids)].copy()

train_data = train_data[['features', 'series_ep_tags']]
test_data = test_data[['features', 'series_ep_tags']]
all_data = train_data_all[['features', 'series_ep_tags', 'series_ep_uuid']]

It was not particularly smooth to work with CSV input. Luckily, it was very simple to get things to "just work" with parquet file inputs. 

If you'll notice, we write out both pre-split data (train/test dfs) and all of the data. This is simply to demonstrate that we can work with pre-split data or we can create a training/eval split as part of our training pipeline. This will be demonstrated below. 

In [7]:
_data_root_split = "gs://ml-sandbox-tagging-tfx-experiments/data/split/"
_data_root_all = "gs://ml-sandbox-tagging-tfx-experiments/data/all/"

In [ ]:
_train_path = os.path.join(_data_root_split, "train.parquet")
_eval_path = os.path.join(_data_root_split, "eval.parquet")

_all_data_path = os.path.join(_data_root_all, "all_data.parquet")

train_data.to_parquet(_train_path, index=False)
test_data.to_parquet(_eval_path, index=False)
all_data.to_parquet(_all_data_path, index=False)

In [ ]:
print(len(train_data))
print(len(test_data))
print(len(all_data))
all_data.head()

`series_ep_uuid` is left in `all_data` in order to create a training/eval split without leakage. This column is obviously not needed for the other two dataframes. 

---
---
# Training Pipeline 

We are now ready to begin our training pipeline. 

### **Creating the Interactive Context**

**The following cell contains utilities for interacting with the metadata store**. Code is adapted from [this repo](https://github.com/tensorflow/tfx/tree/master/tfx/examples/airflow_workshop/notebooks)

The metadata store is one of the most important aspects of using TFX pipelines, and it is important to get some insight into what is going on. [This tutorial](https://www.tensorflow.org/tfx/tutorials/mlmd/mlmd_tutorial) is a good place to start. 

The MLMD database stores three types of metadata:
 + Metadata about the pipeline and lineage information associated with the pipeline components
 + Metadata about artifacts that were generated during the pipeline run
 + Metadata about the executions of the pipeline

In [3]:
class ReadonlyMetadataStore(object):
    """An ml-metadata store that provides read-only methods for notebooks."""

    def __init__(self, store, base_dir):
        """Initializes a ReadonlyMetadataStore with given store.
        Args:
          store: An instance of `metadata_store.MetadataStore`.
        """
        self.metadata_store = store
        self.base_dir = base_dir
        
    def display_types(self):
        # Helper function to render dataframes for the artifact and execution types
        table = {'id': [], 'name': []}
        types = self.metadata_store.get_artifact_types()
        for a_type in types:
            table['id'].append(a_type.id)
            table['name'].append(a_type.name)
        return pd.DataFrame(data=table)
    
    def display_artifacts(self, artifacts):
        # Helper function to render dataframes for the input artifacts
        table = {'artifact id': [], 'type': [], 'uri': []}
        for a in artifacts:
            table['artifact id'].append(a.id)
            artifact_type = self.metadata_store.get_artifact_types_by_id([a.type_id])[0]
            table['type'].append(artifact_type.name)
            table['uri'].append(a.uri.replace(self.base_dir, './'))
        return pd.DataFrame(data=table)
    
    @staticmethod
    def display_properties(node):
        # Helper function to render dataframes for artifact and execution properties
        table = {'property': [], 'value': []}
        for k, v in node.properties.items():
            table['property'].append(k)
            table['value'].append(
            v.string_value if v.HasField('string_value') else v.int_value)
        for k, v in node.custom_properties.items():
            table['property'].append(k)
            table['value'].append(
            v.string_value if v.HasField('string_value') else v.int_value)
        return pd.DataFrame(data=table)

    def get_df_from_single_artifact_or_execution(self, obj):
        """Returns a `pd.DataFrame` based on an artifact/execution properties.
        Args:
          obj: An instance of `metadata_store_pb2.Artifact` or
               `metadata_store_pb2.Execution`.
        Returns:
          A `pd.DataFrame` to display the properties of an artifact/execution.
        """
        data = {}
        if isinstance(obj, metadata_store_pb2.Artifact):
            data['URI'] = obj.uri
        for p in obj.properties:
            data[p.upper()] = _get_value_str(obj.properties[p])
        for p in obj.custom_properties:
            data[p.upper()] = _get_value_str(obj.custom_properties[p])
        return pd.DataFrame.from_dict(
            data=data, orient='index', columns=['']).fillna('-')

    def get_df_from_artifacts_or_executions(self, objects):
        """Returns a `pd.DataFrame` of given artifacts'/executions' properties."""
        data = {}
        for obj in objects:
            col_map = {}
            if isinstance(obj, metadata_store_pb2.Artifact):
                col_map['URI'] = obj.uri
            for p in obj.properties:
                col_map[p.upper()] = _get_value_str(obj.properties[p])
            for p in obj.custom_properties:
                col_map[p.upper()] = _get_value_str(obj.custom_properties[p])
            data[obj.id] = col_map
        df = pd.DataFrame.from_dict(data=data, orient='index').fillna('-')
        df.index.name = 'ID'
        return df

    def get_artifact_df(self, artifact_id):
        """Returns a `pd.DataFrame` for an artifact with `artifact_id`.
        Args:
          artifact_id: An `int` indicating the id of an artifact in the store.
        Returns:
          A `pd.DataFrame` to display the properties of the artifact corresponding
          to `artifact_id` or None if no such artifact exists in the store.
        """
        artifacts = self.metadata_store.get_artifacts_by_id([artifact_id])
        return (
            self.get_df_from_single_artifact_or_execution(artifacts[0])
            if artifacts else None
        )

    def get_execution_df(self, execution_id):
        """Returns a `pd.DataFrame` for an execution with `execution_id`.
        Args:
          execution_id: An `int` indicating the id of an execution in the store.
        Returns:
          A `pd.DataFrame` to display the properties of the execution corresponding
          to `execution_id` or None if no such execution exists in the store.
        """
        executions = self.metadata_store.get_executions_by_id([execution_id])
        return (
            self.get_df_from_single_artifact_or_execution(executions[0])
            if executions else None
        )

    def get_artifacts_of_type_df(self, type_name):
        """Returns a `pd.DataFrame` for all artifacts of given `type_name`.
        Args:
          type_name: A `str` indicating the name of an artifact type in the store.
        Returns:
          A `pd.DataFrame` to display the properties of all artifacts with given
          type in the store.
        """
        return self.get_df_from_artifacts_or_executions(
            self.metadata_store.get_artifacts_by_type(type_name))

    def get_executions_of_type_df(self, type_name):
        """Returns a `pd.DataFrame` for all executions of given `type_name`.
        Args:
          type_name: A `str` indicating the name of an execution type in the store.
        Returns:
          A `pd.DataFrame` to display the properties of all executions with given
          type in the store.
        """
        return self.get_df_from_artifacts_or_executions(
            self.metadata_store.get_executions_by_type(type_name))

    def get_source_artifact_of_type(self, artifact_id, source_type_name):
        """Returns the source artifact of `source_type_name` for `artifact_id`.
        This method recursively traverses the events and associated executions that
        led to generating `artifact_id` to find an artifact of type
        `source_type_name` that was an input for these events.
        Args:
          artifact_id: A `int` indicating the id of an artifact.
          source_type_name: A `str` indicating the type of an artifact that is
              a direct or indirect input for generating `artifact_id`.
        Returns:
          A `metadata_store_pb2.Artifact` of type `source_type_name` that is a
          direct/indirect input for generating `artifact_id` or `None` if no such
          artifact exists.
        """
        a_events = self.metadata_store.get_events_by_artifact_ids([artifact_id])
        for a_event in a_events:
            if _is_input_event(a_event):
                continue
            [execution] = self.metadata_store.get_executions_by_id(
              [a_event.execution_id])
            e_events = self.metadata_store.get_events_by_execution_ids([execution.id])
            for e_event in e_events:
                if _is_output_event(e_event):
                    continue
            [artifact] = self.metadata_store.get_artifacts_by_id(
                [e_event.artifact_id])
            [artifact_type] = self.metadata_store.get_artifact_types_by_id(
                [artifact.type_id])
            if artifact_type.name == source_type_name:
                return artifact
            input_artifact = self.get_source_artifact_of_type(
                artifact.id, source_type_name)
            if input_artifact:
                return input_artifact

    def get_dest_artifact_of_type(self, artifact_id, dest_type_name):
        """Returns the destination artifact of `dest_type_name` from `artifact_id`.
        This method recursively traverses the events and associated executions that
        consumed `artifact_id` to find an artifact of type `dest_type_name` that was
        an output for these events.
        Args:
          artifact_id: A `int` indicating the id of an artifact.
          dest_type_name: A `str` indicating the type of an artifact that is
              a output of an event that directly/indirectly consumed `artifact_id`.
        Returns:
          A `metadata_store_pb2.Artifact` of type `dest_type_name` that is a
          direct/indirect output from `artifact_id` or `None` if no such artifact
          exists.
        """
        a_events = self.metadata_store.get_events_by_artifact_ids([artifact_id])
        for a_event in a_events:
            if _is_output_event(a_event):
                continue
            [execution] = self.metadata_store.get_executions_by_id(
              [a_event.execution_id])
            e_events = self.metadata_store.get_events_by_execution_ids(
              [execution.id])
            for e_event in e_events:
                if _is_input_event(e_event):
                    continue
                [artifact] = self.metadata_store.get_artifacts_by_id(
                [e_event.artifact_id])
                [artifact_type] = self.metadata_store.get_artifact_types_by_id(
                [artifact.type_id])
                if artifact_type.name == dest_type_name:
                    return artifact
                dest_artifact = self.get_dest_artifact_of_type(
                    artifact.id, dest_type_name)
            if dest_artifact:
                return dest_artifact

    def get_execution_for_output_artifact(self, artifact_id, type_name):
        """Returns the execution of `type_name` that generated `artifact_id`.
        Args:
          artifact_id: A `int` indicating the id of an artifact.
          type_name: A `str` indicating the type of an Execution that generated
            `artifact_id`.
        Returns:
          A `metadata_store_pb2.Execution` of type `type_name` that generated
          `artifact_id` or `None` if no such execution exists.
        """
        a_events = self.metadata_store.get_events_by_artifact_ids([artifact_id])
        for a_event in a_events:
            if _is_input_event(a_event):
                continue
            [execution] = self.metadata_store.get_executions_by_id(
              [a_event.execution_id])
            [execution_type] = self.metadata_store.get_execution_types_by_id(
              [execution.type_id])
            if execution_type.name == type_name:
                return execution


def _is_input_event(event):
    return event.type in [metadata_store_pb2.Event.DECLARED_INPUT, 
                          metadata_store_pb2.Event.INPUT]

def _get_value_str(p):
    """Returns a string representation of a `metadata_store_pb2.Value` object."""
    if p.int_value:
        return str(p.int_value)
    if p.string_value:
        return p.string_value
    if p.double_value:
        return str(p.double_value)
    return ''

def _is_output_event(event):
    return event.type == metadata_store_pb2.Event.OUTPUT 

class TFXArtifactTypes(object):
    """Constants for different TFX artifact type names."""
    EXAMPLES = 'Examples'
    SCHEMA = 'Schema'
    EXAMPLE_STATS = 'ExampleStatistics'
    EXAMPLE_VALIDATION = 'ExampleAnomalies'
    TRANSFORMED_EXAMPLES = 'TransformGraph'
    MODEL = 'Model'
    MODEL_EVAL = 'ModelEvaluation'


class TFXExecutionTypes(object):
    """Constants for different TFX execution type names."""
    EXAMPLE_GEN = 'tfx.components.example_gen.component.FileBasedExampleGen'
    STATISTICS_GEN = 'tfx.components.statistics_gen.component.StatisticsGen'
    SCHEMA_GEN = 'tfx.components.schema_gen.component.SchemaGen'
    EXAMPLE_VALIDATION = 'tfx.components.example_validator.component.ExampleValidator'
    TRANSFORM = 'tfx.components.transform.component.Transform'
    TRAINER = 'tfx.components.trainer.component.Trainer'
    EVALUATOR = 'tfx.components.evaluator.component.Evaluator'
    PUSHER = 'tfx.components.pusher.component.Pusher'

In [4]:
_pipeline_root = tempfile.mkdtemp(prefix='pipeline')
_pipeline_name = 'interactive_pipeline'

context = InteractiveContext(pipeline_name=_pipeline_name, pipeline_root=_pipeline_root)

As we can see in the warning above, we will store everything in an ephemeral SQLite database. Again, in a production deployment we would probably use a database within our training cluster (already created as part of a kubeflow deployment) or a managed alternative such as Cloud SQL.

**NOTE:** Be sure to update the location of the sqlite file. 

In [5]:
connection_config = metadata_store_pb2.ConnectionConfig()
connection_config.sqlite.filename_uri = '/tmp/pipelinee9qkzxjt/metadata.sqlite' # REPLACE with new location
connection_config.sqlite.connection_mode = 3 #READWRITE_OPENCREATE
store = metadata_store.MetadataStore(connection_config)
base_dir = connection_config.sqlite.filename_uri.split('metadata.sqlite')[0]

read_only_store = ReadonlyMetadataStore(store, base_dir)

---
### **ExampleGen**

The first component of a training pipeline is usually the ExampleGen component. This component can take pre-split data (input split) or split the data into training and evaluation sets (output split). It will also convert the data into tf.Example format. 

ExampleGen can take in data from different sources, including from CSV files and directly from BigQuery. In this particular case, we use the `parquet_executor` custom executor in order to read Parquet files. 

#### Split the Output

In [8]:
# Use series_ep_uuid to split, exactly as above
output = example_gen_pb2.Output(
                split_config=example_gen_pb2.SplitConfig(splits=[
                    example_gen_pb2.SplitConfig.Split(name='train', hash_buckets=9),
                    example_gen_pb2.SplitConfig.Split(name='eval', hash_buckets=1)
                ],
                partition_feature_name='series_ep_uuid'))


example_gen = FileBasedExampleGen(input_base=_data_root_all, 
                                  custom_executor_spec=executor_spec.ExecutorClassSpec(parquet_executor.Executor),
                                  output_config=output)

context.run(example_gen)

ExecutionResult(
    component_id: FileBasedExampleGen
    execution_id: 1
    outputs:
        examples: Channel(
            type_name: Examples
            artifacts: [Artifact(artifact: id: 1
        type_id: 5
        uri: "/tmp/pipelinee9qkzxjt/FileBasedExampleGen/examples/1"
        properties {
          key: "split_names"
          value {
            string_value: "[\"train\", \"eval\"]"
          }
        }
        custom_properties {
          key: "input_fingerprint"
          value {
            string_value: "split:single_split,num_files:1,total_bytes:35727068,xor_checksum:1603286998,sum_checksum:1603286998"
          }
        }
        custom_properties {
          key: "payload_format"
          value {
            string_value: "FORMAT_TF_EXAMPLE"
          }
        }
        custom_properties {
          key: "span"
          value {
            string_value: "0"
          }
        }
        custom_properties {
          key: "state"
          value {
            string_value: "published"
          }
        }
        , artifact_type: id: 5
        name: "Examples"
        properties {
          key: "span"
          value: INT
        }
        properties {
          key: "split_names"
          value: STRING
        }
        properties {
          key: "version"
          value: INT
        }
        )]
        ))

There are a few different ways to inspect the output of a component. We can try to get the outputs of a component directly from it:

In [127]:
artifact = example_gen.outputs['examples'].get()[0]
print(artifact.split_names, artifact.uri)

["train", "eval"] /tmp/pipelinee9qkzxjt/FileBasedExampleGen/examples/2


We can also interact with the metadata store:

In [128]:
print(store.get_artifacts_by_type('Examples'))

[id: 1
type_id: 5
uri: "/tmp/pipelinee9qkzxjt/FileBasedExampleGen/examples/1"
properties {
  key: "split_names"
  value {
    string_value: "[\"train\", \"eval\"]"
  }
}
custom_properties {
  key: "input_fingerprint"
  value {
    string_value: "split:single_split,num_files:1,total_bytes:35727068,xor_checksum:1603286998,sum_checksum:1603286998"
  }
}
custom_properties {
  key: "payload_format"
  value {
    string_value: "FORMAT_TF_EXAMPLE"
  }
}
custom_properties {
  key: "span"
  value {
    string_value: "0"
  }
}
custom_properties {
  key: "state"
  value {
    string_value: "published"
  }
}
create_time_since_epoch: 1603345794332
last_update_time_since_epoch: 1603345820951
, id: 2
type_id: 5
uri: "/tmp/pipelinee9qkzxjt/FileBasedExampleGen/examples/2"
properties {
  key: "split_names"
  value {
    string_value: "[\"train\", \"eval\"]"
  }
}
custom_properties {
  key: "input_fingerprint"
  value {
    string_value: "split:train,num_files:1,total_bytes:31656086,xor_checksum:16032869

We can also use our custom read only store with extra convenience methods for displaying outputs:

In [129]:
display(read_only_store.get_artifacts_of_type_df(TFXArtifactTypes.EXAMPLES))
display(read_only_store.get_executions_of_type_df(TFXExecutionTypes.EXAMPLE_GEN))

URI        SPLIT_NAMES  \
ID                                                                         
1   /tmp/pipelinee9qkzxjt/FileBasedExampleGen/exam...  ["train", "eval"]   
2   /tmp/pipelinee9qkzxjt/FileBasedExampleGen/exam...  ["train", "eval"]   
7   /tmp/pipelinee9qkzxjt/Transform/transformed_ex...  ["train", "eval"]   

       PAYLOAD_FORMAT SPAN                                  INPUT_FINGERPRINT  \
ID                                                                              
1   FORMAT_TF_EXAMPLE    0  split:single_split,num_files:1,total_bytes:357...   
2   FORMAT_TF_EXAMPLE    0  split:train,num_files:1,total_bytes:31656086,x...   
7                   -    -                                                  -   

        STATE PRODUCER_COMPONENT                  NAME  
ID                                                      
1   published                  -                     -  
2   published                  -                     -  
7   published          Transform  transformed_examples

COMPONENT_ID CUSTOM_CONFIG          PIPELINE_ROOT  \
ID                                                             
1   FileBasedExampleGen          None  /tmp/pipelinee9qkzxjt   
2   FileBasedExampleGen          None  /tmp/pipelinee9qkzxjt   

                                           INPUT_BASE     STATE  \
ID                                                                
1   gs://ml-sandbox-tagging-tfx-experiments/data/all/  complete   
2   gs://ml-sandbox-tagging-tfx-experiments/data/s...  complete   

   OUTPUT_DATA_FORMAT         PIPELINE_NAME SPAN  \
ID                                                 
1                   6  interactive_pipeline    0   
2                   6  interactive_pipeline    0   

                                         INPUT_CONFIG  \
ID                                                      
1   {\n  "splits": [\n    {\n      "name": "single...   
2   {\n  "splits": [\n    {\n      "name": "train"...   

                        RUN_ID  \
ID                               
1   2020-10-22T05:49:54.134230   
2   2020-10-22T05:50:37.565544   

                                        OUTPUT_CONFIG VERSION  \
ID                                                              
1   {\n  "split_config": {\n    "partition_feature...    None   
2                                                  {}    None   

                                    INPUT_FINGERPRINT  
ID                                                     
1   split:single_split,num_files:1,total_bytes:357...  
2   split:train,num_files:1,total_bytes:31656086,x...

Yet another way to display (we could easily change the custom class we created to display in another way, this is just for demonstration purposes):

In [12]:
display(read_only_store.display_types())

examples = store.get_artifacts_by_type("Examples")
display(read_only_store.display_artifacts(examples))

example = examples[-1]
display(read_only_store.display_properties(example))

id      name
0   5  Examples

artifact id      type                               uri
0            1  Examples  ./FileBasedExampleGen/examples/1

property                                              value
0        split_names                                  ["train", "eval"]
1     payload_format                                  FORMAT_TF_EXAMPLE
2  input_fingerprint  split:single_split,num_files:1,total_bytes:357...
3              state                                          published
4               span                                                  0

Now we can see why those utils above were helpful :). The metadata store is very important, but unfortunately it can be a bit difficult to navigate without some extra utilities.

Because we are working in an interactive context, we can do a bit more and directly interact with the outputs of the example gen component. For example, we can create a `tf.data` dataset from the TFRecord files we created. 

In [122]:
def make_dataset(examples, split):
    """
    Create a dataset from examples artifact
    """
    uri = os.path.join(examples.get()[0].uri, split)
    
    tfrecord_filenames = [os.path.join(uri, name) for name in os.listdir(uri)]
    dataset = tf.data.TFRecordDataset(tfrecord_filenames, compression_type="GZIP")
    
    return dataset

In [14]:
train_dataset = make_dataset(example_gen.outputs['examples'], 'train')
eval_dataset = make_dataset(example_gen.outputs['examples'], 'eval')

print('TRAIN DATASET SIZE: {}'.format(train_dataset.reduce(0, lambda x, _: x + 1)))
print('EVAL DATASET SIZE: {}'.format(eval_dataset.reduce(0, lambda x, _: x + 1)))

print('{:=^80}'.format(' Example '))

# Iterate over the first record and decode it.
for tfrecord in train_dataset.take(1):
    serialized_example = tfrecord.numpy()
    example = tf.train.Example()
    example.ParseFromString(serialized_example)
    pp.pprint(example)

TRAIN DATASET SIZE: 90185
EVAL DATASET SIZE: 8907
=================================== Example ====================================
features {
  feature {
    key: "features"
    value {
      bytes_list {
        value: "Ein amerikanischer Milit\303\244rbeamter untersucht den Tod einer Hubschrauberpilotin im Golfkrieg von 1990, um zu entscheiden, ob ihre Handlungen eine posthume Ehrenmedaille verdienen. In der Zwischenzeit versucht er, sich mit einem tragischen Vorfall auseinanderzusetzen, den er w\303\244hrend des Konflikts selbst verursacht und vertuscht hat. Drama mit Denzel Washington, Meg Ryan, Lou Diamond Phillips, Scott Glenn und Matt Damon. .. Krieg Theater. Courage Under Fire  "
      }
    }
  }
  feature {
    key: "series_ep_tags"
    value {
      bytes_list {
        value: "20th century"
        value: "thriller"
        value: "the middle east"
        value: "mystery"
        value: "gulf war"
        value: "war"
        value: "1990s"
        value: "ethics & moralit

We see that we can split the data by supplying an output config. The split isn't exactly the same as the one previously used (which was a result of using sklearn's `train_test_split`). For the rest of the pipeline let's use the pre-split data. 

#### Pre-Split Input

Here we are providing an **input config** specifying that our data is already split. 

In [15]:
input_config = example_gen_pb2.Input(splits=[
                    example_gen_pb2.Input.Split(name='train', pattern='train*'),
                    example_gen_pb2.Input.Split(name='eval', pattern='eval*')
])

example_gen = FileBasedExampleGen(input_base=_data_root_split, 
                                  custom_executor_spec=executor_spec.ExecutorClassSpec(parquet_executor.Executor),
                                  input_config=input_config)

context.run(example_gen)

ExecutionResult(
    component_id: FileBasedExampleGen
    execution_id: 2
    outputs:
        examples: Channel(
            type_name: Examples
            artifacts: [Artifact(artifact: id: 2
        type_id: 5
        uri: "/tmp/pipelinee9qkzxjt/FileBasedExampleGen/examples/2"
        properties {
          key: "split_names"
          value {
            string_value: "[\"train\", \"eval\"]"
          }
        }
        custom_properties {
          key: "input_fingerprint"
          value {
            string_value: "split:train,num_files:1,total_bytes:31656086,xor_checksum:1603286996,sum_checksum:1603286996\nsplit:eval,num_files:1,total_bytes:2420590,xor_checksum:1603286996,sum_checksum:1603286996"
          }
        }
        custom_properties {
          key: "payload_format"
          value {
            string_value: "FORMAT_TF_EXAMPLE"
          }
        }
        custom_properties {
          key: "span"
          value {
            string_value: "0"
          }
        }
        custom_properties {
          key: "state"
          value {
            string_value: "published"
          }
        }
        , artifact_type: id: 5
        name: "Examples"
        properties {
          key: "span"
          value: INT
        }
        properties {
          key: "split_names"
          value: STRING
        }
        properties {
          key: "version"
          value: INT
        }
        )]
        ))

In [16]:
display(read_only_store.get_artifacts_of_type_df(TFXArtifactTypes.EXAMPLES))
display(read_only_store.get_executions_of_type_df(TFXExecutionTypes.EXAMPLE_GEN))

URI        SPLIT_NAMES  \
ID                                                                         
1   /tmp/pipelinee9qkzxjt/FileBasedExampleGen/exam...  ["train", "eval"]   
2   /tmp/pipelinee9qkzxjt/FileBasedExampleGen/exam...  ["train", "eval"]   

       PAYLOAD_FORMAT      STATE SPAN  \
ID                                      
1   FORMAT_TF_EXAMPLE  published    0   
2   FORMAT_TF_EXAMPLE  published    0   

                                    INPUT_FINGERPRINT  
ID                                                     
1   split:single_split,num_files:1,total_bytes:357...  
2   split:train,num_files:1,total_bytes:31656086,x...

STATE VERSION         PIPELINE_NAME  \
ID                                           
1   complete    None  interactive_pipeline   
2   complete    None  interactive_pipeline   

                                        OUTPUT_CONFIG  \
ID                                                      
1   {\n  "split_config": {\n    "partition_feature...   
2                                                  {}   

                                           INPUT_BASE  \
ID                                                      
1   gs://ml-sandbox-tagging-tfx-experiments/data/all/   
2   gs://ml-sandbox-tagging-tfx-experiments/data/s...   

                                    INPUT_FINGERPRINT          PIPELINE_ROOT  \
ID                                                                             
1   split:single_split,num_files:1,total_bytes:357...  /tmp/pipelinee9qkzxjt   
2   split:train,num_files:1,total_bytes:31656086,x...  /tmp/pipelinee9qkzxjt   

                                         INPUT_CONFIG SPAN CUSTOM_CONFIG  \
ID                                                                         
1   {\n  "splits": [\n    {\n      "name": "single...    0          None   
2   {\n  "splits": [\n    {\n      "name": "train"...    0          None   

   OUTPUT_DATA_FORMAT         COMPONENT_ID                      RUN_ID  
ID                                                                      
1                   6  FileBasedExampleGen  2020-10-22T05:49:54.134230  
2                   6  FileBasedExampleGen  2020-10-22T05:50:37.565544

Above we can see how the metadata store gets updated upon running a component. This functionality can allow us to track new data as well as different pipeline runs. 

We can confirm that the dataset sizes are as expected:

In [17]:
train_dataset = make_dataset(example_gen.outputs['examples'], 'train')
eval_dataset = make_dataset(example_gen.outputs['examples'], 'eval')

print('TRAIN DATASET SIZE: {}'.format(train_dataset.reduce(0, lambda x, _: x + 1)))
print('EVAL DATASET SIZE: {}'.format(eval_dataset.reduce(0, lambda x, _: x + 1)))

TRAIN DATASET SIZE: 90543
EVAL DATASET SIZE: 8549


Now we can see that the dataset sizes are exactly the same as the pre-split data (see length of dataframes above). 

---

### **Statistics Gen**

StatisticsGen will generate feature statistics over the data. StatisticsGen is using Beam under the hood for scalability. 

The first time we run StatisticsGen, the output will be used to infer a schema (as part of downstream `SchemaGen`). This automatically inferred schema may have some problems with it, in which case we will need to make some manual updates. For future runs of the pipeline, then, we can provide our manually curated schema to the `StatisticsGen` component via an `ImporterNode` component. 

In [18]:
statistics_gen = StatisticsGen(
    examples=example_gen.outputs['examples'])
context.run(statistics_gen)

ExecutionResult(
    component_id: StatisticsGen
    execution_id: 3
    outputs:
        statistics: Channel(
            type_name: ExampleStatistics
            artifacts: [Artifact(artifact: id: 3
        type_id: 7
        uri: "/tmp/pipelinee9qkzxjt/StatisticsGen/statistics/3"
        properties {
          key: "split_names"
          value {
            string_value: "[\"train\", \"eval\"]"
          }
        }
        custom_properties {
          key: "name"
          value {
            string_value: "statistics"
          }
        }
        custom_properties {
          key: "producer_component"
          value {
            string_value: "StatisticsGen"
          }
        }
        custom_properties {
          key: "state"
          value {
            string_value: "published"
          }
        }
        , artifact_type: id: 7
        name: "ExampleStatistics"
        properties {
          key: "span"
          value: INT
        }
        properties {
          key: "split_names"
          value: STRING
        }
        )]
        ))

In [19]:
display(read_only_store.get_artifacts_of_type_df(TFXArtifactTypes.EXAMPLE_STATS))
display(read_only_store.get_executions_of_type_df(TFXExecutionTypes.STATISTICS_GEN))

URI        SPLIT_NAMES  \
ID                                                                        
3   /tmp/pipelinee9qkzxjt/StatisticsGen/statistics/3  ["train", "eval"]   

          NAME      STATE PRODUCER_COMPONENT  
ID                                            
3   statistics  published      StatisticsGen

PIPELINE_ROOT                      RUN_ID   COMPONENT_ID  \
ID                                                                     
3   /tmp/pipelinee9qkzxjt  2020-10-22T05:51:03.213301  StatisticsGen   

       STATE STATS_OPTIONS_JSON         PIPELINE_NAME EXCLUDE_SPLITS  
ID                                                                    
3   complete               None  interactive_pipeline             []

If we want, we can manually inspect the generated statistics using the Tensorflow Data Validation library:

In [20]:
stats_path = statistics_gen.outputs['statistics'].get()[0].uri
train_statistics_path = os.path.join(stats_path, 'train/stats_tfrecord')
eval_statistics_path = os.path.join(stats_path, 'eval/stats_tfrecord')

train_statistics = tfdv.load_statistics(train_statistics_path)
eval_statistics = tfdv.load_statistics(eval_statistics_path)

Instructions for updating:
Use eager execution and: 
`tf.data.TFRecordDataset(path)`


This will allow us to create visualization as in the cell below. [There are a lot of capabilities in the tensorflow data validation library](https://www.tensorflow.org/tfx/data_validation/api_docs/python/tfdv), including the ability to slice on different feature values. 

As is the case with many of the other TFX component libraries, TFDV does not necessarily need to be used in the context of a TFX pipeline. It could easily be used as part of a non-TFX pipeline within custom components in a Kubeflow Pipeline or even for EDA in a completely standalone manner. 

For the latter use-case, we'd perhaps want to keep some of the other fields from the data, such as genre or subgenre. This would allow us to "slice" the data and visualize feature distributions for each of the slices. This could be used, for example, to understand the differences in features between different types of content such as TV or Movies. 

In [21]:
tfdv.visualize_statistics(lhs_statistics=train_statistics,
                          rhs_statistics=eval_statistics)

We can use these visualizations as a preliminary sense-check. It looks like our training and evaluation datasets are relatively similar from looking at the average string length of the features and labels and from looking at the distribution of the number of tags per example. In this case, it seems like there are no obvious problems with using this data split. In other scenarios, however, these visualizations could help alert us to the fact that there is e.g. a lot of missing data for a particular feature or large differences between the training and eval sets. 


We can also directly visualize the statistics without having to explicitly make calls to tfdv. Of course, this will give us fewer opportunities for customization. 

In [22]:
context.show(statistics_gen.outputs['statistics'])

---

### **SchemaGen**

`Schema` in TFX is an instance of the TensorFlow Metadata schema proto. We can use the inferred schema produced by SchemaGen as a starting point. 

Once `SchemaGen` is executed we can find the schema at the following path:
```
<pipeline_root>/SchemaGen/schema/<artifact_id>/schema.pbtxt
```

As mentioned above, this schema proto can then be modified to specify further details about the dataset, making the downstream validation performed in `ExampleValidator` more stringent. 

TFDV can also be used to infer a schema; this is basically what will be happening under the hood in the SchemaGen component. We can try this first just to get an idea of what is going on:

In [23]:
schema = tfdv.infer_schema(train_statistics, infer_feature_shape=True)
tfdv.display_schema(schema)

Type  Presence  Valency Domain
Feature name                                     
'features'        BYTES  required               -
'series_ep_tags'  BYTES  optional  [1,inf)      -

Using the `infer_feature_shape` arg will allow tfdv to infer the shape of a feature. If this is not included, the downstream Tensorflow Transform component using the schema will parse input as a tf.SparseTensor.

Previously, we had the `series_ep_tags` as a variable length feature while `features` was a fixed length feature (see `Preprocessing.ipynb`). In order to use the exact same preprocessing code as before, we should be sure to infer the feature shape so that tensorflow transform knows to not parse `features` as a `tf.SparseTensor`. Otherwise, we must update the preprocessing code in order to make this conversion. 

It is not a huge difference either way, but these small details are good to be aware of when developing. 

In [24]:
infer_schema = SchemaGen(statistics=statistics_gen.outputs['statistics'],
                         infer_feature_shape=True)
context.run(infer_schema)

ExecutionResult(
    component_id: SchemaGen
    execution_id: 4
    outputs:
        schema: Channel(
            type_name: Schema
            artifacts: [Artifact(artifact: id: 4
        type_id: 9
        uri: "/tmp/pipelinee9qkzxjt/SchemaGen/schema/4"
        custom_properties {
          key: "name"
          value {
            string_value: "schema"
          }
        }
        custom_properties {
          key: "producer_component"
          value {
            string_value: "SchemaGen"
          }
        }
        custom_properties {
          key: "state"
          value {
            string_value: "published"
          }
        }
        , artifact_type: id: 9
        name: "Schema"
        )]
        ))

In [25]:
display(read_only_store.get_artifacts_of_type_df(TFXArtifactTypes.SCHEMA))
display(read_only_store.get_executions_of_type_df(TFXExecutionTypes.SCHEMA_GEN))

URI    NAME      STATE  \
ID                                                                
4   /tmp/pipelinee9qkzxjt/SchemaGen/schema/4  schema  published   

   PRODUCER_COMPONENT  
ID                     
4           SchemaGen

PIPELINE_NAME COMPONENT_ID          PIPELINE_ROOT     STATE  \
ID                                                                       
4   interactive_pipeline    SchemaGen  /tmp/pipelinee9qkzxjt  complete   

                        RUN_ID INFER_FEATURE_SHAPE EXCLUDE_SPLITS  
ID                                                                 
4   2020-10-22T05:52:41.878788                True             []

In [26]:
schema_path = os.path.join(infer_schema.outputs['schema'].get()[0].uri, 'schema.pbtxt')

schema = tfdv.load_schema_text(schema_path)
tfdv.display_schema(schema)

Type  Presence  Valency Domain
Feature name                                     
'features'        BYTES  required               -
'series_ep_tags'  BYTES  optional  [1,inf)      -

We see that the output of the `SchemaGen` component is exactly as we'd expect from generating the schema explicitly using tfdv. This is also the point at which we could identify any issues with the auto-generated schema and make any updates as needed. 

---
### **Example Validator**

We can make use of the Example Validator to validate the evaluation data. Again, the ExampleValidator makes heavy use of TFDV to validate the statistics of some splits on input examples against a schema. 

The ExampleValidator component identifies anomalies in training and serving
data by comparing data statistics computed by StatisticsGen component against a schema. The component can be configured to detect different classes of anomalies.

For our particular case the ExampleValidator will help us find certain classes of anomalies, such as: 
 + Large amounts of missing data
 + Data that doesn't conform to the schema 
 
Unfortunately, a lot of the statistics tests used to detect things like data drift skew might not necessarily work as well for our particular use case. This is because these types of tests are most effect on tabular data, where it is much easier to calculate relevant statistics per feature. Nevertheless, there are still some built-in capabilities that we can take advantage of. 

Fortunately, we also have the ability to create **custom components**, as we'll see demonstrated below. Data Validation might be a perfect opportunity for us to leverage this capability since we'll have the freedom to create highly specialized data validation checks. 

In [27]:
validate_stats = ExampleValidator(
    statistics=statistics_gen.outputs['statistics'],
    schema=infer_schema.outputs['schema']
)
context.run(validate_stats)

ExecutionResult(
    component_id: ExampleValidator
    execution_id: 5
    outputs:
        anomalies: Channel(
            type_name: ExampleAnomalies
            artifacts: [Artifact(artifact: id: 5
        type_id: 11
        uri: "/tmp/pipelinee9qkzxjt/ExampleValidator/anomalies/5"
        properties {
          key: "split_names"
          value {
            string_value: "[\"train\", \"eval\"]"
          }
        }
        custom_properties {
          key: "name"
          value {
            string_value: "anomalies"
          }
        }
        custom_properties {
          key: "producer_component"
          value {
            string_value: "ExampleValidator"
          }
        }
        custom_properties {
          key: "state"
          value {
            string_value: "published"
          }
        }
        , artifact_type: id: 11
        name: "ExampleAnomalies"
        properties {
          key: "span"
          value: INT
        }
        properties {
          key: "split_names"
          value: STRING
        }
        )]
        ))

In [28]:
display(read_only_store.get_artifacts_of_type_df(TFXArtifactTypes.EXAMPLE_VALIDATION))
display(read_only_store.get_executions_of_type_df(TFXExecutionTypes.EXAMPLE_VALIDATION))

URI        SPLIT_NAMES  \
ID                                                                         
5   /tmp/pipelinee9qkzxjt/ExampleValidator/anomali...  ["train", "eval"]   

         NAME      STATE PRODUCER_COMPONENT  
ID                                           
5   anomalies  published   ExampleValidator

STATE          PIPELINE_ROOT         PIPELINE_NAME      COMPONENT_ID  \
ID                                                                            
5   complete  /tmp/pipelinee9qkzxjt  interactive_pipeline  ExampleValidator   

   EXCLUDE_SPLITS                      RUN_ID  
ID                                             
5              []  2020-10-22T05:52:44.673008

In [29]:
train_anomalies_path = os.path.join(validate_stats.outputs['anomalies'].get()[0].uri, 'train/anomalies.pbtxt')
eval_anomalies_path = os.path.join(validate_stats.outputs['anomalies'].get()[0].uri, 'eval/anomalies.pbtxt')

train_anomalies = tfdv.load_anomalies_text(train_anomalies_path)
eval_anomalies = tfdv.load_anomalies_text(eval_anomalies_path)

In [30]:
tfdv.display_anomalies(train_anomalies)
tfdv.display_anomalies(eval_anomalies)

Here we didn't find any anomalies, but that is of course because we didn't set particularly stringent checks in the schema. This will be something that we will have to discuss as an engineering team, as well as the potential need for additional custom data validation components. 

---

### **Transform**

The transform component performas data transformations and feature engineering. We won't go into too much detail here, since a lot of this was covered in the `Preprocessing.ipynb`. As we can see below, the preprocessing function is almost exactly the same as before. The main difference now is that the TFX framework will handle a lot of things under the hood for us that we previously had to do ourselves, such as making explicit calls to beam to analyze and/or transform the dataset. 

In general, the transform and trainer components require much more code than any of the other components because of the arbitrary complexity of the feature engineering/training that you might need. 

In [31]:
from tensorflow_transform.tf_metadata import dataset_metadata
from tensorflow_transform.tf_metadata import dataset_schema

In [32]:
_transform_module_file = 'transform.py'

In [33]:
%%writefile {_transform_module_file}

import tensorflow_transform as tft
import tensorflow as tf

SYNOPSIS = 'features'
TAGS = 'series_ep_tags'
MAX_STRING_LENGTH = 277

white_list = '[^äÄöÖüÜßa-zA-Z]'

def _transformed_name(key):
    return key + '_xf'

def clean(text):
    """
    Clean up text input by removing everything but the 
    white-listed characters
    """
    # Encoding needed to keep german characters
    lower = tf.strings.lower(text, 'utf-8')
    cleaned = tf.strings.regex_replace(lower, white_list, ' ')
    cleaned = tf.strings.strip(cleaned)
    # Filter single letters
    clean_1 = tf.strings.regex_replace(cleaned, r'((^|\s)[äÄöÖüÜßa-zA-Z]{1})+\s', ' ')
    # Replace multiple spaces with single space
    final = tf.strings.regex_replace(clean_1, ' +', ' ')

    return final

def preprocessing_fn(inputs):
    """Preprocess input columns into transformed columns."""
    outputs = {}
    
    #text = tf.squeeze(tf.sparse.to_dense(inputs[SYNOPSIS]), axis=1)
    text = tf.squeeze(inputs[SYNOPSIS], axis=1)
    tags = inputs[TAGS]

    cleaned = clean(text)
    text_tokens = tf.compat.v1.string_split(cleaned, ' ', result_type='RaggedTensor')

    text_tokens = text_tokens.to_tensor(shape=[None, MAX_STRING_LENGTH])
    text_indices = tft.compute_and_apply_vocabulary(
        text_tokens, vocab_filename='vocab', num_oov_buckets=1
    )
    
    # compute vocab of tags, do not apply due to serving issues
    _ = tft.vocabulary(tags, vocab_filename='tags')
    
    outputs[_transformed_name(SYNOPSIS)] = text_indices
    outputs['series_ep_tags'] = tags
    
    # Need to transform the name
    return outputs

Overwriting src/transform.py


In [34]:
transform = Transform(
    examples=example_gen.outputs['examples'],
    schema=infer_schema.outputs['schema'],
    module_file='./transform.py'
)
context.run(transform)

Instructions for updating:
Schema is a deprecated, use schema_utils.schema_from_feature_spec to create a `Schema`
Instructions for updating:
Use ref() instead.


Instructions for updating:
This function will only be available through the v1 compatibility library as tf.compat.v1.saved_model.utils.build_tensor_info or tf.compat.v1.saved_model.build_tensor_info.
INFO:tensorflow:Assets added to graph.
INFO:tensorflow:No assets to write.
Type is unsupported, or the types of the items don't match field type in CollectionDef. Note this is a warning and probably safe to ignore.
'Counter' object has no attribute 'name'
Type is unsupported, or the types of the items don't match field type in CollectionDef. Note this is a warning and probably safe to ignore.
'Counter' object has no attribute 'name'
INFO:tensorflow:SavedModel written to: /tmp/pipelinee9qkzxjt/Transform/transform_graph/6/.temp_path/tftransform_tmp/437e441bd2834315ab45c17e9968192b/saved_model.pb
INFO:tensorflow:Assets added to graph.
INFO:tensorflow:No assets to write.
Type is unsupported, or the types of the items don't match field type in CollectionDef. Note this is a warning and probably 

INFO:tensorflow:Saver not created because there are no variables in the graph to restore
INFO:tensorflow:Saver not created because there are no variables in the graph to restore
INFO:tensorflow:Assets added to graph.
INFO:tensorflow:Assets written to: /tmp/pipelinee9qkzxjt/Transform/transform_graph/6/.temp_path/tftransform_tmp/98324625704946c9bd0bff42732e7c42/assets
INFO:tensorflow:SavedModel written to: /tmp/pipelinee9qkzxjt/Transform/transform_graph/6/.temp_path/tftransform_tmp/98324625704946c9bd0bff42732e7c42/saved_model.pb
value: "\n\013\n\tConst_1:0\022\005vocab"

value: "\n\013\n\tConst_3:0\022\004tags"

INFO:tensorflow:Saver not created because there are no variables in the graph to restore
value: "\n\013\n\tConst_1:0\022\005vocab"

value: "\n\013\n\tConst_3:0\022\004tags"

INFO:tensorflow:Saver not created because there are no variables in the graph to restore
value: "\n\013\n\tConst_1:0\022\005vocab"

value: "\n\013\n\tConst_3:0\022\004tags"

INFO:tensorflow:Saver not created 

ExecutionResult(
    component_id: Transform
    execution_id: 6
    outputs:
        transform_graph: Channel(
            type_name: TransformGraph
            artifacts: [Artifact(artifact: id: 6
        type_id: 13
        uri: "/tmp/pipelinee9qkzxjt/Transform/transform_graph/6"
        custom_properties {
          key: "name"
          value {
            string_value: "transform_graph"
          }
        }
        custom_properties {
          key: "producer_component"
          value {
            string_value: "Transform"
          }
        }
        custom_properties {
          key: "state"
          value {
            string_value: "published"
          }
        }
        , artifact_type: id: 13
        name: "TransformGraph"
        )]
        )
        transformed_examples: Channel(
            type_name: Examples
            artifacts: [Artifact(artifact: id: 7
        type_id: 5
        uri: "/tmp/pipelinee9qkzxjt/Transform/transformed_examples/6"
        properties {
          key: "split_names"
          value {
            string_value: "[\"train\", \"eval\"]"
          }
        }
        custom_properties {
          key: "name"
          value {
            string_value: "transformed_examples"
          }
        }
        custom_properties {
          key: "producer_component"
          value {
            string_value: "Transform"
          }
        }
        custom_properties {
          key: "state"
          value {
            string_value: "published"
          }
        }
        , artifact_type: id: 5
        name: "Examples"
        properties {
          key: "span"
          value: INT
        }
        properties {
          key: "split_names"
          value: STRING
        }
        properties {
          key: "version"
          value: INT
        }
        )]
        )
        updated_analyzer_cache: Channel(
            type_name: TransformCache
            artifacts: [Artifact(artifact: id: 8
        type_id: 14
        uri: "/tmp/pipelinee9qkzxjt/Transform/updated_analyzer_cache/6"
        custom_properties {
          key: "name"
          value {
            string_value: "updated_analyzer_cache"
          }
        }
        custom_properties {
          key: "producer_component"
          value {
            string_value: "Transform"
          }
        }
        custom_properties {
          key: "state"
          value {
            string_value: "published"
          }
        }
        , artifact_type: id: 14
        name: "TransformCache"
        )]
        ))

In [35]:
display(read_only_store.get_artifacts_of_type_df('transform_graph'))
display(read_only_store.get_executions_of_type_df(TFXExecutionTypes.TRANSFORM))

Empty DataFrame
Columns: []
Index: []

SPLITS_CONFIG COMPONENT_ID                      CHECKSUM_MD5  \
ID                                                                
6           None    Transform  cfe18b0395e74c64d6c3ba6fabb9fa57   

            PIPELINE_ROOT     STATE PREPROCESSING_FN CUSTOM_CONFIG  \
ID                                                                   
6   /tmp/pipelinee9qkzxjt  complete             None          null   

                        RUN_ID         PIPELINE_NAME     MODULE_FILE  
ID                                                                    
6   2020-10-22T05:52:48.829887  interactive_pipeline  ./transform.py

After we have run the transform, we can inspect the newly created features. 

In [126]:
transform_dir = transform.outputs['transform_graph'].get()[0].uri
transformed_schema = tfdv.load_schema_text(os.path.join(transform_dir, 'transformed_metadata', 'schema.pbtxt'))

tfdv.display_schema(schema)
tfdv.display_schema(transformed_schema)

Type  Presence  Valency Domain
Feature name                                     
'features'        BYTES  required               -
'series_ep_tags'  BYTES  optional  [1,inf)      -

Type  Presence Valency      Domain
Feature name                                         
'features_xf'       INT  required          [0,128973]
'series_ep_tags'  BYTES                             -

As we can see, the actual features have gone from being strings to integers. We have changed the name in order to reflect this transformation. The `series_ep_tags` field is unchanged, but we have created a vocabulary for the tags that we can use during training, as we'll see in the next cell. 

Just like with the outputs of the `ExampleGen` component, we can inspect the outputs of the `Transform` component: 

In [36]:
train_dataset_transformed = make_dataset(transform.outputs['transformed_examples'], 'train')
eval_dataset_transformed = make_dataset(transform.outputs['transformed_examples'], 'eval')

print('TRAIN DATASET SIZE: {}'.format(train_dataset_transformed.reduce(0, lambda x, _: x + 1)))
print('EVAL DATASET SIZE: {}'.format(eval_dataset_transformed.reduce(0, lambda x, _: x + 1)))


tf_transform_output = tft.TFTransformOutput(transform.outputs['transform_graph'].get()[0].uri)

VOCAB_FILE = tf_transform_output.vocabulary_file_by_name('vocab')
TAG_FILE = tf_transform_output.vocabulary_file_by_name('tags')

vocab_df = pd.read_csv(VOCAB_FILE, header=None)
tags_df = pd.read_csv(TAG_FILE, header=None)

for raw_record in train_dataset_transformed.take(1):
    print('\n {:=^80} \n'.format(" Serialized "))
    print(raw_record)
    print('\n {:=^80} \n'.format(" Decoded "))
    print(tf.io.parse_single_example(raw_record, tf_transform_output.transformed_feature_spec()))
    
display(vocab_df)
display(tags_df)

TRAIN DATASET SIZE: 90543
EVAL DATASET SIZE: 8549

 ================================== Serialized ================================== 

tf.Tensor(b"\n\xba\x07\n\xaf\x01\n\x0eseries_ep_tags\x12\x9c\x01\n\x99\x01\n\x0c20th century\n\x08thriller\n\x0fthe middle east\n\x07mystery\n\x08gulf war\n\x03war\n\x051990s\n\x11ethics & morality\n\x12military personnel\n\x06action\n\x05drama\n\x08military\n\x0fofficer-colonel\n\x85\x06\n\x0bfeatures_xf\x12\xf5\x05\x1a\xf2\x05\n\xef\x05\n\xbb\x0b\xfa\xf9\x05\x90\x01\x0c\xfb\x01\x14\xaa\xc4\x06\x19\xd3\xa7\x03\x05\x10\x04\xab\x07\xce\x02\x1d\xc4\x1d\x0b\xf8\xcd\x05\xe2\x9d\x04\xe9\x06\x03\x02\xcc\x03H\x16\x0e\x06\x12\x9f+\xad\x1e\xf1%\x0c\x16'\x1a\xf6W\x95\x03\xf9\t\x00\xfe\xaf\x01#4\x06\xc2\x83\x01\x85\x08\xcc'\xb5\x03\xd9\x18\xdf2\xf9\x1c\xd2\x05\x81\x1e\x00\xae\x02\x86\x0b\x94\x04,\xd0\xd5\x02g\xf5\x06\xcd\xef\x07\xcd\xef\x07\xcd\xef\x07\xcd\xef\x07\xcd\xef\x07\xcd\xef\x07\xcd\xef\x07\xcd\xef\x07\xcd\xef\x07\xcd\xef\x07\xcd\xef\x07\xcd\xef\x07\xcd\x

0
0             und
1             die
2             der
3              in
4              zu
...           ...
128968       aalt
128969     aakeel
128970      aafri
128971     aaargh
128972  aaaaaaaah

[128973 rows x 1 columns]

0
0                  usa
1                drama
2              factual
3       united kingdom
4              reality
...                ...
2591  2010-11 football
2592  2009-10 football
2593  2000-01 football
2594  1999-00 football
2595  1992-93 football

[2596 rows x 1 columns]

Compare this result to that found in the `Preprocessing.ipynb` notebook, they're exactly the same! We also see how we can access the vocabularies created during the transform phase: 

```python
tf_transform_output = tft.TFTransformOutput(transform.outputs['transform_graph'].get()[0].uri)
```

Since we pass the transform output in as an argument to the trainer component, we will have access to this information in the trainer. 

---

### **Trainer**

The Trainer component is responsible for actually training the model. It is roughly equivalent to the `trainer.task.py` file we would typically write for submitting a training job to AI platform. We can in fact integrate TFX with AI platform, both for training and serving. This requires the use of a custom tfx executor. As with `Transform`, we will need to provide a module file that defines our custom logic for this component. 

In [38]:
_trainer_module_file = 'model.py'

The following has been pulled out of the `Trainer.ipynb` notebook to create a self-contained module file that the Trainer component will reference. The Trainer will be looking for a `run_fn` as an entry point to the training logic. 

In [58]:
%%writefile {_trainer_module_file}
import tensorflow as tf
import tensorflow_transform as tft
import pandas as pd
import numpy as np

from tensorflow.keras import callbacks, layers
from tensorflow.keras.losses import BinaryCrossentropy
from tensorflow.keras.models import Model, Sequential
from tensorflow.keras.optimizers import Adam
from tensorflow.keras.metrics import Precision, Recall

from google.cloud import storage
import pickle

EMBEDDING_LOCATION = 'gs://ml-sandbox-101-tagging/data/processed/training_data/glove_data/glove_embedding_index.pkl'
MAX_STRING_LENGTH = 277


def create_tag_lookup_table(tag_file):
    table = tf.lookup.StaticVocabularyTable(
        tf.lookup.TextFileInitializer(
            tag_file,
            key_dtype=tf.string, key_index=tf.lookup.TextFileIndex.WHOLE_LINE,
            value_dtype=tf.int64, value_index=tf.lookup.TextFileIndex.LINE_NUMBER,
            delimiter=None),
        num_oov_buckets=1)
    return table


def label_transform(x, y, num_tags, table):
    """Use the number of classes to convert the sparse tag indicies to dense"""
    # Need to add one for out-of-vocabulary tags in eval dataset
    return (x, tf.cast(tf.sparse.to_indicator(table.lookup(y), vocab_size=num_tags + 1), tf.int32))

def _gzip_reader_fn(filenames):
    """Small utility returning a record reader that can read gzip'ed fies"""
    return tf.data.TFRecordDataset(filenames, compression_type="GZIP")


def _input_fn(file_pattern, tf_transform_output, num_tags, table, batch_size=64, shuffle=True, epochs=None):
    """Generates features and label for tuning/training.
    Args:
        file_pattern: input tfrecord file pattern.
        tf_transform_output: A TFTransformOutput.
        batch_size: representing the number of consecutive elements of
          returned dataset to combine in a single batch
    Returns:
        A dataset that contains (features, indices) tuple where features
        is a dictionary of Tensors, and indices is a single Tensor of
        label indices.
    """
    transformed_feature_spec = (
        tf_transform_output.transformed_feature_spec().copy()
    )

    dataset = tf.data.experimental.make_batched_features_dataset(
        file_pattern=file_pattern,
        batch_size=batch_size,
        features=transformed_feature_spec,
        reader=_gzip_reader_fn,
        shuffle=shuffle,
        label_key='series_ep_tags',
        num_epochs=epochs
    )
    return dataset.map(lambda x, y: label_transform(x, y, num_tags, table))

class AutoTaggingModel:
    def __init__(
        self,
        embedding_file,
        embedding_dim,
        train_embedding,
        output_size,
        vocab_size,
        vocab_df,
        max_string_length,
    ):
        self.__embedding_file = embedding_file
        self.__embedding_dim = embedding_dim
        self.__vocab_size = vocab_size
        self.__vocab_df = vocab_df
        self.__train_embedding = train_embedding
        self.__output_size = output_size
        self.__max_string_length = max_string_length
        
        self.__initialize_embedding_matrix()
    
    def __initialize_embedding_matrix(self):
        storage_client = storage.Client()
        
        # Better way to do this with os.path?
        split_path = self.__embedding_file.split('/')
        bucket_name = split_path[2]
        blob_name = ('/').join(split_path[3:])
        
        bucket = storage_client.bucket(bucket_name)
        blob = bucket.blob(blob_name)
        
        pickle_in = blob.download_as_string()
        file = pickle.loads(pickle_in)
        
        self.embedding_matrix = np.zeros((self.__vocab_size, 
                                     self.__embedding_dim))
        
        for i, word in enumerate(self.__vocab_df.values):
            embedding_vector = file.get(word[0])
            if embedding_vector is not None:
                self.embedding_matrix[i] = embedding_vector
        
    def embedding_layer(self):
        return layers.Embedding(
            input_dim=self.__vocab_size,
            output_dim=self.__embedding_dim,
            weights=[self.embedding_matrix],
            input_length=self.__max_string_length,
            trainable=self.__train_embedding,
        )

    def n_grams_channel(self, inputs, n_words_filter: int):
        channel = layers.Conv2D(256, kernel_size=(n_words_filter, self.__embedding_dim), activation="relu")(inputs)
        channel_mp = layers.MaxPool2D(pool_size=(channel.shape[1], 1))(channel)
        channel_final = layers.Flatten()(channel_mp)
        return channel_final
    
    def define_model(self):
        inputs = layers.Input(shape=(self.__max_string_length,), name='features')
        embedding = self.embedding_layer()(inputs) 
        channel_inputs = layers.Reshape(target_shape=(self.__max_string_length, self.__embedding_dim, 1))(embedding)
        channel1_final = self.n_grams_channel(channel_inputs, 3)
        channel2_final = self.n_grams_channel(channel_inputs, 4)
        channel3_final = self.n_grams_channel(channel_inputs, 5)
        channels_final = layers.Concatenate()(
            [channel1_final, channel2_final, channel3_final]
        )
        channels_final = layers.Dropout(rate=0.4)(channels_final)
        channels_final = layers.Dense(2000, "relu")(channels_final)
        predictions = layers.Dense(self.__output_size, "sigmoid")(channels_final)
        model = Model(inputs=inputs, outputs=predictions)

        return model

    def get_model(self):
        strategy = tf.distribute.MirroredStrategy()
        with strategy.scope():
            model = self.define_model()

            metrics = [tf.keras.metrics.Precision(), tf.keras.metrics.Recall()]
            model.compile(
                optimizer=tf.keras.optimizers.Adam(learning_rate=0.0005),
                loss=BinaryCrossentropy(),
                metrics=metrics,
            )
        return model

    
def _get_serve_tf_examples_fn(model, tf_transform_output):
    """Returns a function that parses a serialized tf.Example."""

    model.tft_layer = tf_transform_output.transform_features_layer()

    @tf.function
    def serve_tf_examples_fn(serialized_tf_examples):
        """Returns the output to be used in the serving signature."""
        feature_spec = tf_transform_output.raw_feature_spec()
        feature_spec.pop('series_ep_tags')
        
        parsed_features = tf.io.parse_example(
            serialized_tf_examples, feature_spec
        )

        transformed_features = model.tft_layer(parsed_features)

        outputs = model(transformed_features)
        return {"outputs": outputs}

    return serve_tf_examples_fn


def run_fn(fn_args):
    """Train the model based on given args
    
    Args:
        fn_args: Holds args used to train the model as name/value pairs
    """
    tf_transform_output = tft.TFTransformOutput(fn_args.transform_output)
    
    num_tags = tf_transform_output.vocabulary_size_by_name('tags')
    tag_file = tf_transform_output.vocabulary_file_by_name('tags')
    vocab_size = tf_transform_output.vocabulary_size_by_name('vocab')
    vocab_file = tf_transform_output.vocabulary_file_by_name('vocab')
    vocab_df = pd.read_csv(vocab_file, header=None)
    
    table = create_tag_lookup_table(tag_file)
    
    train_dataset = _input_fn(
        file_pattern=fn_args.train_files,
        tf_transform_output=tf_transform_output,
        num_tags=num_tags,
        table=table,
        batch_size=64)

    eval_dataset = _input_fn(
        file_pattern=fn_args.eval_files,
        tf_transform_output=tf_transform_output,
        batch_size=64,
        num_tags=num_tags,
        table=table)
    
    model = AutoTaggingModel(
        embedding_dim=300,
        train_embedding=True,
        embedding_file=EMBEDDING_LOCATION,
        output_size=num_tags + 1,
        vocab_size=vocab_size + 1,
        vocab_df=vocab_df,
        max_string_length=MAX_STRING_LENGTH).get_model()
    
    early_stopping_callback = callbacks.EarlyStopping(monitor='val_loss',
        min_delta=0.0001,
        patience=4,
        verbose=0,  
        mode='auto',  
        restore_best_weights=True)  

    reduce_lr = callbacks.ReduceLROnPlateau(
        monitor='val_loss', 
        factor=0.1, 
        patience=2, 
        verbose=0, 
        mode='auto',
        min_delta=0.0001) 
    
    history = model.fit(
        train_dataset, 
        epochs=10,
        steps_per_epoch=fn_args.train_steps / 10, 
        validation_data=eval_dataset,
        validation_steps=fn_args.eval_steps,
        callbacks=[early_stopping_callback, reduce_lr]
    )
    
    signatures = {
        "serving_default": _get_serve_tf_examples_fn(model, tf_transform_output).get_concrete_function(
            tf.TensorSpec(shape=[None], dtype=tf.string, name="examples")
        ),
    }
    
    model.save(
        fn_args.serving_model_dir, save_format="tf", signatures=signatures
    )

In [40]:
!mkdir serving_test

mkdir: cannot create directory ‘serving_test’: File exists


First we can try training for a few steps outside of the context of the TFX pipeline:

In [41]:
from dataclasses import dataclass
from src.trainer.model import run_fn 

@dataclass
class function_args:
    """Class for creating function args for run fn."""
    train_files: str
    eval_files: str
    transform_output: str
    serving_model_dir: str
    train_steps: int
    eval_steps: int
        
train_files = os.path.join(transform.outputs['transformed_examples'].get()[0].uri, 'train/*')
eval_files = os.path.join(transform.outputs['transformed_examples'].get()[0].uri, 'eval/*')
transform_output = transform.outputs['transform_graph'].get()[0].uri
serving_model_dir = 'serving_test/'

fn_args = function_args(train_files, eval_files, transform_output, serving_model_dir, 10, 1)

In [42]:
run_fn(fn_args)

Epoch 1/10
1/1 [==============================] - ETA: 0s - loss: 0.6933 - precision: 0.0038 - recall: 0.50 - 1s 789ms/step - loss: 0.6933 - precision: 0.0038 - recall: 0.5072 - val_loss: 0.6748 - val_precision: 0.0034 - val_recall: 0.2396
Epoch 2/10
1/1 [==============================] - ETA: 0s - loss: 0.6741 - precision: 0.0045 - recall: 0.29 - 1s 505ms/step - loss: 0.6741 - precision: 0.0045 - recall: 0.2905 - val_loss: 0.6361 - val_precision: 0.0041 - val_recall: 0.1111
Epoch 3/10
1/1 [==============================] - ETA: 0s - loss: 0.6346 - precision: 0.0041 - recall: 0.12 - 1s 509ms/step - loss: 0.6346 - precision: 0.0041 - recall: 0.1294 - val_loss: 0.5621 - val_precision: 0.0072 - val_recall: 0.0512
Epoch 4/10
1/1 [==============================] - ETA: 0s - loss: 0.5560 - precision: 0.0056 - recall: 0.05 - 1s 517ms/step - loss: 0.5560 - precision: 0.0056 - recall: 0.0505 - val_loss: 0.4489 - val_precision: 0.0094 - val_recall: 0.0113
Epoch 5/10
1/1 [========================

Now we can try running it locally via the trainer component.

In [72]:
trainer = Trainer(
    module_file=os.path.abspath(_trainer_module_file),
    custom_executor_spec=executor_spec.ExecutorClassSpec(GenericExecutor),
    examples=transform.outputs['transformed_examples'],
    transform_graph=transform.outputs['transform_graph'],
    schema=infer_schema.outputs['schema'],
    train_args=trainer_pb2.TrainArgs(num_steps=10),
    eval_args=trainer_pb2.EvalArgs(num_steps=1))
context.run(trainer)

ExecutionResult(
    component_id: Trainer
    execution_id: 19
    outputs:
        model: Channel(
            type_name: Model
            artifacts: [Artifact(artifact: id: 9
        type_id: 16
        uri: "/tmp/pipelinee9qkzxjt/Trainer/model/7"
        custom_properties {
          key: "name"
          value {
            string_value: "model"
          }
        }
        custom_properties {
          key: "producer_component"
          value {
            string_value: "Trainer"
          }
        }
        custom_properties {
          key: "state"
          value {
            string_value: "published"
          }
        }
        create_time_since_epoch: 1603346283832
        last_update_time_since_epoch: 1603346323990
        , artifact_type: id: 16
        name: "Model"
        )]
        )
        model_run: Channel(
            type_name: ModelRun
            artifacts: [Artifact(artifact: id: 10
        type_id: 17
        uri: "/tmp/pipelinee9qkzxjt/Trainer/model_run/7"
        custom_properties {
          key: "name"
          value {
            string_value: "model_run"
          }
        }
        custom_properties {
          key: "producer_component"
          value {
            string_value: "Trainer"
          }
        }
        custom_properties {
          key: "state"
          value {
            string_value: "published"
          }
        }
        create_time_since_epoch: 1603346283832
        last_update_time_since_epoch: 1603346323990
        , artifact_type: id: 17
        name: "ModelRun"
        )]
        ))

In [44]:
display(read_only_store.get_artifacts_of_type_df(TFXArtifactTypes.MODEL))
display(read_only_store.get_executions_of_type_df(TFXExecutionTypes.TRAINER))

URI      STATE PRODUCER_COMPONENT   NAME
ID                                                                            
9   /tmp/pipelinee9qkzxjt/Trainer/model/7  published            Trainer  model

MODULE_FILE RUN_FN TRAINER_FN  \
ID                                                                        
7   /home/jupyter/autotagging-tfx/src/trainer/mode...   None       None   

                        RUN_ID               EVAL_ARGS          PIPELINE_ROOT  \
ID                                                                              
7   2020-10-22T05:58:03.796702  {\n  "num_steps": 1\n}  /tmp/pipelinee9qkzxjt   

   COMPONENT_ID         PIPELINE_NAME     STATE CUSTOM_CONFIG  \
ID                                                              
7       Trainer  interactive_pipeline  complete          null   

                 TRAIN_ARGS                      CHECKSUM_MD5  
ID                                                             
7   {\n  "num_steps": 10\n}  687ffa3ef67e6d1c7854a65fc922b8f2

In [45]:
!ls {trainer.outputs['model'].get()[0].uri}/serving_model_dir
!ls {trainer.outputs['model'].get()[0].uri}/serving_model_dir/assets

assets	saved_model.pb	variables
tags  vocab


#### **AI Platform Trainer**

We can also run the training on AI platform using a custom executor. Unfortunately I don't think you can run this from the interactive context, though. This is still here just to demonstrate what the call to AI Platform could look like. 

Something similar can be down with a custom pusher executor in order to serve the model using AI platform. 

In [46]:
from tfx.orchestration import data_types
from tfx.extensions.google_cloud_ai_platform.trainer import (executor as aip_trainer_executor)

In [51]:
ai_platform_training_args = {}

ai_platform_training_args['project'] = 'ml-sandbox-101'
ai_platform_training_args['region'] = 'europe-west2'
ai_platform_training_args['masterType'] = 'n1-standard-16'
ai_platform_training_args['masterConfig'] = {'acceleratorConfig': {'count': 1,
                                                                   'type': 'NVIDIA_TESLA_T4'}}

ai_platform_training_args['scaleTier'] = 'CUSTOM'

In [53]:
module_file_gs = 'gs://ml-sandbox-tagging-tfx-experiments/code/module.py'

In [54]:
!gsutil cp {_trainer_module_file} {module_file_gs}

Copying file://src/trainer/model.py [Content-Type=text/x-python]...
/ [1 files][  8.7 KiB/  8.7 KiB]                                                
Operation completed over 1 objects/8.7 KiB.                                      


In [71]:
aip_trainer = Trainer(
    module_file=module_file_gs,
    custom_executor_spec=executor_spec.ExecutorClassSpec(aip_trainer_executor.GenericExecutor),
    custom_config={aip_trainer_executor.TRAINING_ARGS_KEY: ai_platform_training_args},
    examples=transform.outputs['transformed_examples'],
    transform_graph=transform.outputs['transform_graph'],
    schema=infer_schema.outputs['schema'],
    train_args=trainer_pb2.TrainArgs(num_steps=10),
    eval_args=trainer_pb2.EvalArgs(num_steps=1))
context.run(aip_trainer)

HttpError: <HttpError 400 when requesting https://ml.googleapis.com/v1/projects/ml-sandbox-101/jobs?alt=json returned "Field: package_uris Error: Tarball URIs of the training program must be provided.". Details: "[{'@type': 'type.googleapis.com/google.rpc.BadRequest', 'fieldViolations': [{'field': 'package_uris', 'description': 'Tarball URIs of the training program must be provided.'}]}]">

---

### **Validation**

In order to analyze model performance using the TensorFlow Model Analysis library, we would normally use the `Evaluator` component. It can analyze performance on particular subsets of the eval dataset as based on the `slices` defined by the developer. There are a lot of good out-of-the-box capabilities for both Data and Model validation within the TFX libraries that we can take advantage of. Unfortunately the standard evaluator component is a little difficult to work with for this particular model due to the assumptions TFX makes about the data and model. 

As a result, we need to create a custom evaluator. This would have probably been required regardless, however, seeing as we would probably want a large number of custom tests (including behavioral tests) to be run on this particular model. 

In the `Evaluation.ipynb` notebook we used the simple threshold-based validation that was also used in the original research notebooks. In those notebooks, a hard-coded threshold of 0.7 for precision and 0.4 for recall on the evaluation data was set as a gate for pushing the model. We can replicate this here. 

Of course, in the future we will want many more tests, and ideally these tests should be **behavioral** in nature, as opposed to testing whether certain ML-metrics reach some arbitrary threshold. Due to the specific nature of this model, a qualititative evaluation of model performance is going to be more informative than quantitative checks on particular loss metrics. Nevertheless, we can still have some of these quantitative checks as a first step. 

In [73]:
from tfx.dsl.component.experimental.annotations import OutputDict
from tfx.dsl.component.experimental.annotations import InputArtifact
from tfx.dsl.component.experimental.annotations import OutputArtifact
from tfx.dsl.component.experimental.annotations import Parameter
from tfx.dsl.component.experimental.decorators import component

from tfx.types.standard_artifacts import Examples
from tfx.types.standard_artifacts import ModelBlessing
from tfx.types import standard_artifacts

from tensorflow.keras.models import load_model

In [74]:
from model import *

The following cell contains the logic we'd want to replicate in our custom validator component. 

In [75]:
model = load_model(os.path.join(trainer.outputs['model'].get()[0].uri, 'serving_model_dir'))
    
tf_transform_output = tft.TFTransformOutput(transform.outputs['transform_graph'].get()[0].uri)
num_tags = tf_transform_output.vocabulary_size_by_name('tags')
tag_file = tf_transform_output.vocabulary_file_by_name('tags')

eval_files = os.path.join(transform.outputs['transformed_examples'].get()[0].uri, 'eval/*')
table = create_tag_lookup_table(tag_file)

eval_dataset = _input_fn(
    file_pattern=eval_files,
    tf_transform_output=tf_transform_output,
    batch_size=64,
    epochs=1,
    num_tags=num_tags,
    table=table,
    shuffle=False
)

results = model.evaluate(eval_dataset)

134/134 [==============================]0.0344 - precision_1: 0.0000e+00 - recall_1: 0.0000e+0 - 0s 127ms/step - loss: 0.0338 - precision_1: 0.0000e+00 - recall_1: 0.0000e+0 - 1s 171ms/step - loss: 0.0328 - precision_1: 0.0000e+00 - recall_1: 0.0000e+0 - 1s 194ms/step - loss: 0.0320 - precision_1: 0.0000e+00 - recall_1: 0.0000e+0 - 1s 212ms/step - loss: 0.0320 - precision_1: 0.0000e+00 - recall_1: 0.0000e+0 - 1s 218ms/step - loss: 0.0317 - precision_1: 0.0000e+00 - recall_1: 0.0000e+0 - 2s 224ms/step - loss: 0.0313 - precision_1: 0.0000e+00 - recall_1: 0.0000e+0 - 2s 228ms/step - loss: 0.0311 - precision_1: 0.0000e+00 - recall_1: 0.0000e+0 - 2s 231ms/step - loss: 0.0308 - precision_1: 0.0000e+00 - recall_1: 0.0000e+0 - 2s 234ms/step - loss: 0.0307 - precision_1: 0.0000e+00 - recall_1: 0.0000e+0 - 3s 235ms/step - loss: 0.0309 - precision_1: 0.0000e+00 - recall_1: 0.0000e+0 - 3s 236ms/step - loss: 0.0312 - precision_1: 0.0000e+00 - recall_1: 0.0000e+0 - 3s 238ms/step - loss: 0.0312 - pre

In [76]:
from tfx.utils import io_utils
from tfx.utils import path_utils

Below is our custom validation component. Notice we use the standard artifacts as input and output in order to effectively communicate with the metadata store and with downstream components (such as pusher) that would rely on the output of a typical evaluator component. 

Notice that we have very limited capability here, such as no comparison to previous models or slicing on different feature values. These capabilities will need to be explored later. 

In [107]:
@component
def ThresholdValidator(
    model: InputArtifact[standard_artifacts.Model],
    transform_graph: InputArtifact[standard_artifacts.TransformGraph],
    transform_examples: InputArtifact[standard_artifacts.Examples],
    blessing: OutputArtifact[standard_artifacts.ModelBlessing],
    recall_threshold: Parameter[float] = 0.4,
    precision_threshold: Parameter[float] = 0.7, 
    ) -> OutputDict(precision=float, recall=float):
    '''Simple custom model validation component.'''
    
    loaded_model = load_model(os.path.join(model.uri, 'serving_model_dir'))
    
    tf_transform_output = tft.TFTransformOutput(transform_graph.uri)
    num_tags = tf_transform_output.vocabulary_size_by_name('tags')
    tag_file = tf_transform_output.vocabulary_file_by_name('tags')
    
    eval_files = os.path.join(transform_examples.uri, 'eval/*')
    table = create_tag_lookup_table(tag_file)
    
    eval_dataset = _input_fn(
        file_pattern=eval_files,
        tf_transform_output=tf_transform_output,
        batch_size=64,
        epochs=1,
        num_tags=num_tags,
        table=table,
        shuffle=False
    )
    results = loaded_model.evaluate(eval_dataset)
    
    if (results[1] >= precision_threshold) and (results[2] >= recall_threshold):
        io_utils.write_string_file(os.path.join(blessing.uri, 'BLESSED'), '')
        blessing.set_int_custom_property('blessed', 1)
    else:
        io_utils.write_string_file(os.path.join(blessing.uri, 'NOT_BLESSED'), '')
        blessing.set_int_custom_property('blessed', 0)
        

    return {
        'precision': results[1],
        'recall': results[2]
    }

First we can create a component with the same threshold as before. 

In [103]:
validator_strict = ThresholdValidator(
    model=trainer.outputs['model'],
    transform_graph=transform.outputs['transform_graph'],
    transform_examples=transform.outputs['transformed_examples'],
    recall_threshold=0.4,
    precision_threshold=0.7)
context.run(validator_strict)

ExecutionResult(
    component_id: ThresholdValidator
    execution_id: 27
    outputs:
        blessing: Channel(
            type_name: ModelBlessing
            artifacts: [Artifact(artifact: id: 36
        type_id: 19
        uri: "/tmp/pipelinee9qkzxjt/ThresholdValidator/blessing/26"
        custom_properties {
          key: "blessed"
          value {
            int_value: 0
          }
        }
        custom_properties {
          key: "name"
          value {
            string_value: "blessing"
          }
        }
        custom_properties {
          key: "producer_component"
          value {
            string_value: "ThresholdValidator"
          }
        }
        custom_properties {
          key: "state"
          value {
            string_value: "published"
          }
        }
        create_time_since_epoch: 1603351673980
        last_update_time_since_epoch: 1603351713462
        , artifact_type: id: 19
        name: "ModelBlessing"
        )]
        )
        precision: Channel(
            type_name: Float
            artifacts: [Artifact(artifact: id: 37
        type_id: 20
        uri: "/tmp/pipelinee9qkzxjt/ThresholdValidator/precision/26/value"
        custom_properties {
          key: "name"
          value {
            string_value: "precision"
          }
        }
        custom_properties {
          key: "producer_component"
          value {
            string_value: "ThresholdValidator"
          }
        }
        custom_properties {
          key: "state"
          value {
            string_value: "published"
          }
        }
        create_time_since_epoch: 1603351673981
        last_update_time_since_epoch: 1603351713462
        , artifact_type: id: 20
        name: "Float"
        )]
        )
        recall: Channel(
            type_name: Float
            artifacts: [Artifact(artifact: id: 38
        type_id: 20
        uri: "/tmp/pipelinee9qkzxjt/ThresholdValidator/recall/26/value"
        custom_properties {
          key: "name"
          value {
            string_value: "recall"
          }
        }
        custom_properties {
          key: "producer_component"
          value {
            string_value: "ThresholdValidator"
          }
        }
        custom_properties {
          key: "state"
          value {
            string_value: "published"
          }
        }
        create_time_since_epoch: 1603351673981
        last_update_time_since_epoch: 1603351713462
        , artifact_type: id: 20
        name: "Float"
        )]
        ))

In [104]:
!ls {validator_strict.outputs['blessing'].get()[0].uri}

NOT_BLESSED


The model was not blessed, as expected (we only ran training for a few steps). What happens when we have a much lower threshold? 

In [108]:
validator_lax = ThresholdValidator(
    model=trainer.outputs['model'],
    transform_graph=transform.outputs['transform_graph'],
    transform_examples=transform.outputs['transformed_examples'],
    recall_threshold=0.0,
    precision_threshold=0.0)
context.run(validator_lax)

134/134 [==============================]0.0344 - precision_1: 0.0000e+00 - recall_1: 0.0000e+0 - 0s 150ms/step - loss: 0.0338 - precision_1: 0.0000e+00 - recall_1: 0.0000e+0 - 1s 191ms/step - loss: 0.0328 - precision_1: 0.0000e+00 - recall_1: 0.0000e+0 - 1s 210ms/step - loss: 0.0320 - precision_1: 0.0000e+00 - recall_1: 0.0000e+0 - 1s 223ms/step - loss: 0.0320 - precision_1: 0.0000e+00 - recall_1: 0.0000e+0 - 1s 230ms/step - loss: 0.0317 - precision_1: 0.0000e+00 - recall_1: 0.0000e+0 - 2s 236ms/step - loss: 0.0313 - precision_1: 0.0000e+00 - recall_1: 0.0000e+0 - 2s 240ms/step - loss: 0.0311 - precision_1: 0.0000e+00 - recall_1: 0.0000e+0 - 2s 244ms/step - loss: 0.0308 - precision_1: 0.0000e+00 - recall_1: 0.0000e+0 - 2s 247ms/step - loss: 0.0307 - precision_1: 0.0000e+00 - recall_1: 0.0000e+0 - 3s 249ms/step - loss: 0.0309 - precision_1: 0.0000e+00 - recall_1: 0.0000e+0 - 3s 251ms/step - loss: 0.0312 - precision_1: 0.0000e+00 - recall_1: 0.0000e+0 - 3s 252ms/step - loss: 0.0312 - pre

ExecutionResult(
    component_id: ThresholdValidator
    execution_id: 29
    outputs:
        blessing: Channel(
            type_name: ModelBlessing
            artifacts: [Artifact(artifact: id: 42
        type_id: 19
        uri: "/tmp/pipelinee9qkzxjt/ThresholdValidator/blessing/29"
        custom_properties {
          key: "blessed"
          value {
            int_value: 1
          }
        }
        custom_properties {
          key: "name"
          value {
            string_value: "blessing"
          }
        }
        custom_properties {
          key: "producer_component"
          value {
            string_value: "ThresholdValidator"
          }
        }
        custom_properties {
          key: "state"
          value {
            string_value: "published"
          }
        }
        , artifact_type: id: 19
        name: "ModelBlessing"
        )]
        )
        precision: Channel(
            type_name: Float
            artifacts: [Artifact(artifact: id: 43
        type_id: 20
        uri: "/tmp/pipelinee9qkzxjt/ThresholdValidator/precision/29/value"
        custom_properties {
          key: "name"
          value {
            string_value: "precision"
          }
        }
        custom_properties {
          key: "producer_component"
          value {
            string_value: "ThresholdValidator"
          }
        }
        custom_properties {
          key: "state"
          value {
            string_value: "published"
          }
        }
        , artifact_type: id: 20
        name: "Float"
        )]
        )
        recall: Channel(
            type_name: Float
            artifacts: [Artifact(artifact: id: 44
        type_id: 20
        uri: "/tmp/pipelinee9qkzxjt/ThresholdValidator/recall/29/value"
        custom_properties {
          key: "name"
          value {
            string_value: "recall"
          }
        }
        custom_properties {
          key: "producer_component"
          value {
            string_value: "ThresholdValidator"
          }
        }
        custom_properties {
          key: "state"
          value {
            string_value: "published"
          }
        }
        , artifact_type: id: 20
        name: "Float"
        )]
        ))

In [109]:
!ls {validator_lax.outputs['blessing'].get()[0].uri}

BLESSED


Now the model is blessed! Does this component interact with the Pusher correctly? 

---
### **Pusher**

The final component is the Pusher, where we actually push our validated model to a deployment target, in this case a bucket in GCS which TFS/KFS will be listening to in order to pick up the latest model. 

First we can check if the model gets pushed if we use the results from the strict validator:

In [115]:
pusher = Pusher(
  model=trainer.outputs['model'],
  model_blessing=validator_strict.outputs['blessing'],
  push_destination=pusher_pb2.PushDestination(
    filesystem=pusher_pb2.PushDestination.Filesystem(
        base_directory=serving_model_dir)
  )
)
context.run(pusher)

ExecutionResult(
    component_id: Pusher
    execution_id: 30
    outputs:
        pushed_model: Channel(
            type_name: PushedModel
            artifacts: [Artifact(artifact: id: 45
        type_id: 23
        uri: "/tmp/pipelinee9qkzxjt/Pusher/pushed_model/30"
        custom_properties {
          key: "name"
          value {
            string_value: "pushed_model"
          }
        }
        custom_properties {
          key: "producer_component"
          value {
            string_value: "Pusher"
          }
        }
        custom_properties {
          key: "pushed"
          value {
            int_value: 0
          }
        }
        custom_properties {
          key: "state"
          value {
            string_value: "published"
          }
        }
        , artifact_type: id: 23
        name: "PushedModel"
        )]
        ))

In [117]:
!ls {pusher.outputs['pushed_model'].get()[0].uri}

It looks like nothing was written out! Seems to be a good sign. 

In [116]:
display(read_only_store.get_artifacts_of_type_df('PushedModel'))
display(read_only_store.get_executions_of_type_df(TFXExecutionTypes.PUSHER))

URI PUSHED      STATE  \
ID                                                                   
45  /tmp/pipelinee9qkzxjt/Pusher/pushed_model/30         published   

            NAME PRODUCER_COMPONENT  
ID                                   
45  pushed_model             Pusher

PUSH_DESTINATION CUSTOM_CONFIG  \
ID                                                                    
30  {\n  "filesystem": {\n    "base_directory": "s...          null   

                        RUN_ID     STATE COMPONENT_ID         PIPELINE_NAME  \
ID                                                                            
30  2020-10-22T07:37:20.202789  complete       Pusher  interactive_pipeline   

            PIPELINE_ROOT  
ID                         
30  /tmp/pipelinee9qkzxjt

Now we can try again using the results of the lax model validator. 

In [118]:
pusher_lax = Pusher(
  model=trainer.outputs['model'],
  model_blessing=validator_lax.outputs['blessing'],
  push_destination=pusher_pb2.PushDestination(
    filesystem=pusher_pb2.PushDestination.Filesystem(
        base_directory=serving_model_dir)
  )
)
context.run(pusher_lax)

ExecutionResult(
    component_id: Pusher
    execution_id: 31
    outputs:
        pushed_model: Channel(
            type_name: PushedModel
            artifacts: [Artifact(artifact: id: 46
        type_id: 23
        uri: "/tmp/pipelinee9qkzxjt/Pusher/pushed_model/31"
        custom_properties {
          key: "name"
          value {
            string_value: "pushed_model"
          }
        }
        custom_properties {
          key: "producer_component"
          value {
            string_value: "Pusher"
          }
        }
        custom_properties {
          key: "pushed"
          value {
            int_value: 1
          }
        }
        custom_properties {
          key: "pushed_destination"
          value {
            string_value: "serving_test/1603352340"
          }
        }
        custom_properties {
          key: "pushed_version"
          value {
            string_value: "1603352340"
          }
        }
        custom_properties {
          key: "state"
          value {
            string_value: "published"
          }
        }
        , artifact_type: id: 23
        name: "PushedModel"
        )]
        ))

In [120]:
!ls {pusher_lax.outputs['pushed_model'].get()[0].uri}

assets	saved_model.pb	variables


Now it looks like something was actually written out! 

In [121]:
display(read_only_store.get_artifacts_of_type_df('PushedModel'))
display(read_only_store.get_executions_of_type_df(TFXExecutionTypes.PUSHER))

URI      STATE  \
ID                                                            
45  /tmp/pipelinee9qkzxjt/Pusher/pushed_model/30  published   
46  /tmp/pipelinee9qkzxjt/Pusher/pushed_model/31  published   

   PRODUCER_COMPONENT PUSHED          NAME       PUSHED_DESTINATION  \
ID                                                                    
45             Pusher         pushed_model                        -   
46             Pusher      1  pushed_model  serving_test/1603352340   

   PUSHED_VERSION  
ID                 
45              -  
46     1603352340

RUN_ID     STATE CUSTOM_CONFIG  \
ID                                                       
30  2020-10-22T07:37:20.202789  complete          null   
31  2020-10-22T07:39:00.629171  complete          null   

                                     PUSH_DESTINATION         PIPELINE_NAME  \
ID                                                                            
30  {\n  "filesystem": {\n    "base_directory": "s...  interactive_pipeline   
31  {\n  "filesystem": {\n    "base_directory": "s...  interactive_pipeline   

   COMPONENT_ID          PIPELINE_ROOT  
ID                                      
30       Pusher  /tmp/pipelinee9qkzxjt  
31       Pusher  /tmp/pipelinee9qkzxjt

This comparison makes it clear that we were actually able to push to the serving directory. 

In [ ]:
!rm model.py transform.py
!rm -rf serving_test/